In [1]:
# feature_{0...129} - represents real stock data. 
# Each row represnts trading opportunity, for which you will be predicting an action value: 1 to make the trade and 0 to pass on it. 
# Weight and resp - represents a return on the trade. 
# date - day of the trade
# ts_id = time ordering
# 

# resp_{1,2,3,4} - returns over different time horizons. 
#

# https://www.kaggle.com/fernandocanteruccio/jane-street-reinforce-agent-exploration -- Solving the problem using Reinforcement learning 

In [2]:
import pandas as pd 
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score

feature_data = pd.read_csv('./features.csv')
feature_data.head()

feature  tag_0  tag_1  tag_2  tag_3  tag_4  tag_5  tag_6  tag_7  tag_8  \
0  feature_0  False  False  False  False  False  False  False  False  False   
1  feature_1  False  False  False  False  False  False   True   True  False   
2  feature_2  False  False  False  False  False  False   True   True  False   
3  feature_3  False  False  False  False  False  False   True  False   True   
4  feature_4  False  False  False  False  False  False   True  False   True   

   ...  tag_19  tag_20  tag_21  tag_22  tag_23  tag_24  tag_25  tag_26  \
0  ...   False   False   False   False   False   False   False   False   
1  ...   False   False   False   False   False   False   False   False   
2  ...   False   False   False   False   False   False   False   False   
3  ...   False   False   False   False   False   False   False   False   
4  ...   False   False   False   False   False   False   False   False   

   tag_27  tag_28  
0   False   False  
1   False   False  
2   False   False  
3   False   False  
4   False   False  

[5 rows x 30 columns]

In [65]:
import pandas as pd

data_train_original = pd.read_csv('./train.csv')
data_train_sliced = data_train_original.head(100000)
data_train_sliced

date     weight    resp_1    resp_2    resp_3    resp_4      resp  \
0         0   0.000000  0.009916  0.014079  0.008773  0.001390  0.006270   
1         0  16.673515 -0.002828 -0.003226 -0.007319 -0.011114 -0.009792   
2         0   0.000000  0.025134  0.027607  0.033406  0.034380  0.023970   
3         0   0.000000 -0.004730 -0.003273 -0.000461 -0.000476 -0.003200   
4         0   0.138531  0.001252  0.002165 -0.001215 -0.006219 -0.002604   
...     ...        ...       ...       ...       ...       ...       ...   
99995    16   0.000000 -0.000567 -0.001869  0.000209  0.005757  0.002378   
99996    16   7.244412 -0.005087 -0.003462  0.003404 -0.002871 -0.007983   
99997    16   0.742093 -0.004017 -0.005074 -0.003260  0.002065  0.000325   
99998    16   0.223989  0.009427  0.014389  0.045104  0.055153  0.038939   
99999    16   2.780260  0.003875  0.008955  0.014597  0.023805  0.022352   

       feature_0  feature_1  feature_2  ...  feature_121  feature_122  \
0              1  -1.872746  -2.191242  ...          NaN     1.168391   
1             -1  -1.349537  -1.704709  ...          NaN    -1.178850   
2             -1   0.812780  -0.256156  ...          NaN     6.115747   
3             -1   1.174378   0.344640  ...          NaN     2.838853   
4              1  -3.172026  -3.093182  ...          NaN     0.344850   
...          ...        ...        ...  ...          ...          ...   
99995          1   1.405669   0.512533  ...    -2.732149    -1.613148   
99996          1   0.430194  -0.403471  ...     0.323771     0.778653   
99997          1  -0.004709  -0.811126  ...    -0.254012     0.456345   
99998         -1  -3.172026  -3.093182  ...     0.797686     1.556671   
99999          1   2.495152   0.955959  ...    -2.441213     0.092483   

       feature_123  feature_124  feature_125  feature_126  feature_127  \
0         8.313583     1.782433    14.018213     2.653056    12.600292   
1         1.777472    -0.915458     2.831612    -1.417010     2.297459   
2         9.667908     5.542871    11.671595     7.281757    10.060014   
3         0.499251     3.033732     1.513488     4.397532     1.266037   
4         4.101145     0.614252     6.623456     0.800129     5.233243   
...            ...          ...          ...          ...          ...   
99995    -2.666405    -1.032045    -3.289939    -1.908938    -2.608201   
99996     0.750449     0.376205     0.477554     0.902297     0.787591   
99997     0.543483    -0.018550    -0.340577     0.010961    -0.252464   
99998    -1.648137     4.397054     1.772141     5.391140     0.932286   
99999    -1.801058     0.141955    -2.572515     0.136312    -1.938826   

       feature_128  feature_129  ts_id  
0         2.301488    11.445807      0  
1        -1.304614     1.898684      1  
2         6.638248     9.427299      2  
3         3.856384     1.013469      3  
4         0.362636     3.926633      4  
...            ...          ...    ...  
99995    -1.629636    -2.242429  99995  
99996     0.857411     0.698640  99996  
99997     0.259685     0.134213  99997  
99998     2.010078    -1.393968  99998  
99999     0.099691    -1.731471  99999  

[100000 rows x 138 columns]

In [66]:
data_train_sliced.to_csv('train_sliced2.csv',index=False)

In [2]:
import pandas as pd
from xgboost import XGBClassifier
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score

data_train_raw = pd.read_csv('./train_sliced2.csv')

In [3]:
#subsetting dataframe
#data_train_raw.head()

data_train_subset = data_train_raw[['weight','resp_1','resp_2','resp_3','resp_4','resp']]
#data_train_subset.head()
data_train = data_train_raw.drop(['weight','resp_1','resp_2','resp_3','resp_4','resp'], axis=1)
data_train.head()

date  feature_0  feature_1  feature_2  feature_3  feature_4  feature_5  \
0     0          1  -1.872746  -2.191242  -0.474163  -0.323046   0.014688   
1     0         -1  -1.349537  -1.704709   0.068058   0.028432   0.193794   
2     0         -1   0.812780  -0.256156   0.806463   0.400221  -0.614188   
3     0         -1   1.174378   0.344640   0.066872   0.009357  -1.006373   
4     0          1  -3.172026  -3.093182  -0.161518  -0.128149  -0.195006   

   feature_6  feature_7  feature_8  ...  feature_121  feature_122  \
0  -0.002484        NaN        NaN  ...          NaN     1.168391   
1   0.138212        NaN        NaN  ...          NaN    -1.178850   
2  -0.354800        NaN        NaN  ...          NaN     6.115747   
3  -0.676458        NaN        NaN  ...          NaN     2.838853   
4  -0.143780        NaN        NaN  ...          NaN     0.344850   

   feature_123  feature_124  feature_125  feature_126  feature_127  \
0     8.313583     1.782433    14.018213     2.653056    12.600292   
1     1.777472    -0.915458     2.831612    -1.417010     2.297459   
2     9.667908     5.542871    11.671595     7.281757    10.060014   
3     0.499251     3.033732     1.513488     4.397532     1.266037   
4     4.101145     0.614252     6.623456     0.800129     5.233243   

   feature_128  feature_129  ts_id  
0     2.301488    11.445807      0  
1    -1.304614     1.898684      1  
2     6.638248     9.427299      2  
3     3.856384     1.013469      3  
4     0.362636     3.926633      4  

[5 rows x 132 columns]

In [4]:
# feature correlation
import seaborn as sns
import matplotlib.pyplot as plt

def correlation_heatmap(train):
    correlations = train.corr()
    fig, ax = plt.subplots(figsize=(100,100))
    sns.heatmap(correlations, vmax=1.0, center=0, fmt='.2f', square=True, linewidth=.7, annot=True, cbar_kws={"shrink":70})
    plt.show()
    return correlations

In [5]:
import numpy as np

def features_selection_based_on_correlation(correlations):
    columns = np.full((correlations.shape[0],), True, dtype=bool)
    for i in range(correlations.shape[0]):
        for j in range(i+1, correlations.shape[0]):
            if correlations.iloc[i,j] >= 0.9: 
                if columns[j]:
                    columns[j] = False
    return columns
    

In [6]:
# EDA on the dataset
# info of the dataset 
data_train.info()


# feature correlation - Heatmap
correlations = correlation_heatmap(data_train)



<class 'pandas.core.frame.DataFrame'>
RangeIndex: 100000 entries, 0 to 99999
Columns: 132 entries, date to ts_id
dtypes: float64(129), int64(3)
memory usage: 100.7 MB


In [7]:
# selection based on correlations
corr = data_train.corr()
columns = features_selection_based_on_correlation(corr)
selected_columns = data_train.columns[columns]

data_train = data_train[selected_columns]

data_train.head()


date  feature_0  feature_1  feature_3  feature_5  feature_7  feature_9  \
0     0          1  -1.872746  -0.474163   0.014688        NaN  -0.989982   
1     0         -1  -1.349537   0.068058   0.193794        NaN  -0.151877   
2     0         -1   0.812780   0.806463  -0.614188        NaN   5.448261   
3     0         -1   1.174378   0.066872  -1.006373        NaN   4.508206   
4     0          1  -3.172026  -0.161518  -0.195006        NaN   2.683018   

   feature_10  feature_11  feature_13  ...  feature_106  feature_109  \
0   -1.055090         NaN   -2.667671  ...     4.147254    -0.892724   
1   -0.384952         NaN    1.225838  ...     1.622137    -1.332492   
2    2.668029         NaN    3.836342  ...     2.156228     1.193823   
3    2.484260         NaN    2.902176  ...    -1.781693     2.513074   
4    1.450991         NaN    1.257761  ...     0.623132    -0.934675   

   feature_111  feature_112  feature_115  feature_117  feature_118  \
0    -0.156332     0.622816     2.561593     3.457757     6.649580   
1    -0.586619    -1.040491     0.983440     1.357907     1.612348   
2     0.097345     0.796214     2.548596     0.882588     1.817895   
3     0.424964     1.992887     0.561528    -0.994041     0.099560   
4    -0.373013    -1.213540     2.684119     2.861848     2.134804   

   feature_120  feature_121  feature_123  
0          NaN          NaN     8.313583  
1          NaN          NaN     1.777472  
2          NaN          NaN     9.667908  
3          NaN          NaN     0.499251  
4          NaN          NaN     4.101145  

[5 rows x 85 columns]

In [8]:
# Do feature engineering
# 1. Check the feature correlations. 
data_train_subset['action'] = ((data_train_subset['weight'].values * data_train_subset['resp'].values) > 0).astype('int')

#concatenate the "Action" in the training data
data_train_final = pd.concat([data_train_subset,data_train], axis=1)
data_train_final.head()

<ipython-input-8-e5b015b66dc0>:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data_train_subset['action'] = ((data_train_subset['weight'].values * data_train_subset['resp'].values) > 0).astype('int')


weight    resp_1    resp_2    resp_3    resp_4      resp  action  date  \
0   0.000000  0.009916  0.014079  0.008773  0.001390  0.006270       0     0   
1  16.673515 -0.002828 -0.003226 -0.007319 -0.011114 -0.009792       0     0   
2   0.000000  0.025134  0.027607  0.033406  0.034380  0.023970       0     0   
3   0.000000 -0.004730 -0.003273 -0.000461 -0.000476 -0.003200       0     0   
4   0.138531  0.001252  0.002165 -0.001215 -0.006219 -0.002604       0     0   

   feature_0  feature_1  ...  feature_106  feature_109  feature_111  \
0          1  -1.872746  ...     4.147254    -0.892724    -0.156332   
1         -1  -1.349537  ...     1.622137    -1.332492    -0.586619   
2         -1   0.812780  ...     2.156228     1.193823     0.097345   
3         -1   1.174378  ...    -1.781693     2.513074     0.424964   
4          1  -3.172026  ...     0.623132    -0.934675    -0.373013   

   feature_112  feature_115  feature_117  feature_118  feature_120  \
0     0.622816     2.561593     3.457757     6.649580          NaN   
1    -1.040491     0.983440     1.357907     1.612348          NaN   
2     0.796214     2.548596     0.882588     1.817895          NaN   
3     1.992887     0.561528    -0.994041     0.099560          NaN   
4    -1.213540     2.684119     2.861848     2.134804          NaN   

   feature_121  feature_123  
0          NaN     8.313583  
1          NaN     1.777472  
2          NaN     9.667908  
3          NaN     0.499251  
4          NaN     4.101145  

[5 rows x 92 columns]

In [9]:
#concatenate the "Action" in the training data
data_train_final = pd.concat([data_train_subset,data_train], axis=1)

data_train_final.head()

weight    resp_1    resp_2    resp_3    resp_4      resp  action  date  \
0   0.000000  0.009916  0.014079  0.008773  0.001390  0.006270       0     0   
1  16.673515 -0.002828 -0.003226 -0.007319 -0.011114 -0.009792       0     0   
2   0.000000  0.025134  0.027607  0.033406  0.034380  0.023970       0     0   
3   0.000000 -0.004730 -0.003273 -0.000461 -0.000476 -0.003200       0     0   
4   0.138531  0.001252  0.002165 -0.001215 -0.006219 -0.002604       0     0   

   feature_0  feature_1  ...  feature_106  feature_109  feature_111  \
0          1  -1.872746  ...     4.147254    -0.892724    -0.156332   
1         -1  -1.349537  ...     1.622137    -1.332492    -0.586619   
2         -1   0.812780  ...     2.156228     1.193823     0.097345   
3         -1   1.174378  ...    -1.781693     2.513074     0.424964   
4          1  -3.172026  ...     0.623132    -0.934675    -0.373013   

   feature_112  feature_115  feature_117  feature_118  feature_120  \
0     0.622816     2.561593     3.457757     6.649580          NaN   
1    -1.040491     0.983440     1.357907     1.612348          NaN   
2     0.796214     2.548596     0.882588     1.817895          NaN   
3     1.992887     0.561528    -0.994041     0.099560          NaN   
4    -1.213540     2.684119     2.861848     2.134804          NaN   

   feature_121  feature_123  
0          NaN     8.313583  
1          NaN     1.777472  
2          NaN     9.667908  
3          NaN     0.499251  
4          NaN     4.101145  

[5 rows x 92 columns]

In [10]:
#clear the NaN Values - Use the mean of the coloum to fill the NaN. 

data_train_final = data_train_final.fillna(data_train_final.mean())
data_train_final.head()

weight    resp_1    resp_2    resp_3    resp_4      resp  action  date  \
0   0.000000  0.009916  0.014079  0.008773  0.001390  0.006270       0     0   
1  16.673515 -0.002828 -0.003226 -0.007319 -0.011114 -0.009792       0     0   
2   0.000000  0.025134  0.027607  0.033406  0.034380  0.023970       0     0   
3   0.000000 -0.004730 -0.003273 -0.000461 -0.000476 -0.003200       0     0   
4   0.138531  0.001252  0.002165 -0.001215 -0.006219 -0.002604       0     0   

   feature_0  feature_1  ...  feature_106  feature_109  feature_111  \
0          1  -1.872746  ...     4.147254    -0.892724    -0.156332   
1         -1  -1.349537  ...     1.622137    -1.332492    -0.586619   
2         -1   0.812780  ...     2.156228     1.193823     0.097345   
3         -1   1.174378  ...    -1.781693     2.513074     0.424964   
4          1  -3.172026  ...     0.623132    -0.934675    -0.373013   

   feature_112  feature_115  feature_117  feature_118  feature_120  \
0     0.622816     2.561593     3.457757     6.649580     0.740222   
1    -1.040491     0.983440     1.357907     1.612348     0.740222   
2     0.796214     2.548596     0.882588     1.817895     0.740222   
3     1.992887     0.561528    -0.994041     0.099560     0.740222   
4    -1.213540     2.684119     2.861848     2.134804     0.740222   

   feature_121  feature_123  
0     0.191642     8.313583  
1     0.191642     1.777472  
2     0.191642     9.667908  
3     0.191642     0.499251  
4     0.191642     4.101145  

[5 rows x 92 columns]

In [11]:
X = data_train_final.loc[:,data_train_final.columns.str.contains('|'.join(['weight','feature']))]
Y = data_train_final.loc[:,'action']

X.head()

weight  feature_0  feature_1  feature_3  feature_5  feature_7  \
0   0.000000          1  -1.872746  -0.474163   0.014688   0.121419   
1  16.673515         -1  -1.349537   0.068058   0.193794   0.121419   
2   0.000000         -1   0.812780   0.806463  -0.614188   0.121419   
3   0.000000         -1   1.174378   0.066872  -1.006373   0.121419   
4   0.138531          1  -3.172026  -0.161518  -0.195006   0.121419   

   feature_9  feature_10  feature_11  feature_13  ...  feature_106  \
0  -0.989982   -1.055090    0.173799   -2.667671  ...     4.147254   
1  -0.151877   -0.384952    0.173799    1.225838  ...     1.622137   
2   5.448261    2.668029    0.173799    3.836342  ...     2.156228   
3   4.508206    2.484260    0.173799    2.902176  ...    -1.781693   
4   2.683018    1.450991    0.173799    1.257761  ...     0.623132   

   feature_109  feature_111  feature_112  feature_115  feature_117  \
0    -0.892724    -0.156332     0.622816     2.561593     3.457757   
1    -1.332492    -0.586619    -1.040491     0.983440     1.357907   
2     1.193823     0.097345     0.796214     2.548596     0.882588   
3     2.513074     0.424964     1.992887     0.561528    -0.994041   
4    -0.934675    -0.373013    -1.213540     2.684119     2.861848   

   feature_118  feature_120  feature_121  feature_123  
0     6.649580     0.740222     0.191642     8.313583  
1     1.612348     0.740222     0.191642     1.777472  
2     1.817895     0.740222     0.191642     9.667908  
3     0.099560     0.740222     0.191642     0.499251  
4     2.134804     0.740222     0.191642     4.101145  

[5 rows x 85 columns]

In [18]:
# https://machinelearningmastery.com/feature-selection-machine-learning-python/

from sklearn.feature_selection import SelectKBest
from sklearn.feature_selection import f_classif
from numpy import set_printoptions

# Univariate selection - select features(X) that has strong relationship with output variable(Y)
# feature extraction
test = SelectKBest(score_func=f_classif, k=4)
fit = test.fit(X, Y)
# summarize scores
set_printoptions(precision=1)
print(fit.scores_)
features = fit.transform(X)
# summarize selected features
print(features[0:5,:])


[3.7e+01 1.8e+01 2.8e+02 2.9e+02 3.5e+01 5.2e+00 2.2e+01 5.5e+00 5.6e+00
 1.8e+01 1.1e+01 2.3e+01 7.3e+01 5.1e+00 1.3e+01 2.3e+02 1.7e+01 4.7e+01
 7.9e+01 1.5e+01 1.7e+01 5.0e-02 4.9e+01 4.8e+00 2.7e-02 2.1e-02 1.8e+01
 8.6e+00 8.7e+00 4.3e+00 1.1e+01 3.5e+00 2.3e+01 9.5e+00 7.8e+00 2.6e-03
 2.5e+01 2.8e+00 2.1e-02 1.2e+01 2.6e+00 4.2e+00 8.8e+00 1.1e+00 6.8e-01
 2.4e+01 3.6e+00 5.1e+00 1.5e+01 4.4e+00 1.7e+00 4.2e+00 4.1e+00 3.8e+00
 1.5e+00 4.9e+01 2.0e+01 2.3e-01 9.8e+00 5.8e+00 2.7e+00 3.9e-01 1.5e+00
 1.5e+01 7.3e-01 1.4e-04 8.9e+00 2.3e+01 5.9e+01 1.9e+01 1.8e+01 4.7e+01
 3.4e-01 2.9e+00 3.0e-01 4.0e+01 2.1e+01 3.7e+01 1.5e+01 2.2e+01 2.8e+01]
[[-0.5  0.  -0.5  1.3]
 [ 0.1  0.2  0.4  0.8]
 [ 0.8 -0.6  0.7  2.3]
 [ 0.1 -1.   0.6  1.7]
 [-0.2 -0.2 -0.2  1.2]]


In [12]:
#split data into train and test dataset

seed = 7
test_size = 0.33
X_train, X_test, y_train, y_test = train_test_split(X,Y, test_size=test_size, random_state=seed)

X_test.head()

weight  feature_0  feature_1  feature_3  feature_5  feature_7  \
33909  0.306346         -1  -3.172026   2.948774   0.013211   1.575999   
92307  0.171994          1  -1.540222   0.279726  -1.474322   3.356802   
89107  0.035917         -1   0.110847  -0.076187  -0.595941  -0.722325   
9538   0.000000          1   6.937090   2.105089   1.925084  -1.492101   
31008  2.750752         -1  -2.502039  -2.877398  -2.858129   1.418981   

       feature_9  feature_10  feature_11  feature_13  ...  feature_106  \
33909   1.004544    0.268851   -4.127715    3.488502  ...    -1.781693   
92307  -0.109338   -0.779403   -1.389769    0.645636  ...     0.849861   
89107   2.278207    0.449798   -0.175454    0.819321  ...    -1.085026   
9538    3.861108    1.594151    1.046157    3.018707  ...     8.528530   
31008  -1.509974   -1.382771   -0.639819   -0.792089  ...    -1.781693   

       feature_109  feature_111  feature_112  feature_115  feature_117  \
33909    -3.548454    -1.315008    -3.807339    -2.922627    -3.071912   
92307    -1.303806     0.749830    -1.730155     0.168164     4.199363   
89107    -0.028628    -0.523476    -0.255237    -1.170040    -2.333119   
9538      0.801107     0.026826     0.434998     6.899294     3.643804   
31008    -2.033625    -0.537853    -2.068670     0.410587     2.314170   

       feature_118  feature_120  feature_121  feature_123  
33909    -3.202494     5.230353     4.817310     4.082042  
92307    -0.264691     0.875287     2.769964     0.154596  
89107    -1.434071     2.635135     1.607046     1.915277  
9538      5.202798    -0.719316     0.398537    -0.351986  
31008     0.703275    -1.684417    -2.358433    -1.578026  

[5 rows x 85 columns]

In [14]:
#https://machinelearningmastery.com/feature-importance-and-feature-selection-with-xgboost-in-python/

from numpy import sort
from sklearn.feature_selection import SelectFromModel


#model = XGBClassifier()

model = XGBClassifier(n_estimators=400, max_depth=20, eta=0.01,missing=None,random_state=42,tree_method='gpu_hist',subsample=0.8, colsample_bytree=1)

model.fit(X_train, y_train)

# make predictions for test data and evaluate
predictions = model.predict(X_test)
accuracy = accuracy_score(y_test, predictions)
print("Accuracy: %.2f%%" % (accuracy * 100.0))

# Calculate feature importance
list(zip(X_train,model.feature_importances_))

Accuracy: 79.81%


[('weight', 0.25120303),
 ('feature_0', 0.0059556183),
 ('feature_1', 0.0075767166),
 ('feature_3', 0.011525405),
 ('feature_5', 0.013987841),
 ('feature_7', 0.00816644),
 ('feature_9', 0.007655303),
 ('feature_10', 0.008120564),
 ('feature_11', 0.0077794814),
 ('feature_13', 0.0075642187),
 ('feature_15', 0.0078049535),
 ('feature_16', 0.008046151),
 ('feature_17', 0.008486662),
 ('feature_19', 0.008427742),
 ('feature_21', 0.008270995),
 ('feature_27', 0.008718045),
 ('feature_29', 0.008380989),
 ('feature_31', 0.008265736),
 ('feature_37', 0.010493157),
 ('feature_39', 0.012175544),
 ('feature_41', 0.014140943),
 ('feature_42', 0.013745705),
 ('feature_43', 0.016110627),
 ('feature_44', 0.012895816),
 ('feature_45', 0.015471797),
 ('feature_46', 0.0077895634),
 ('feature_47', 0.008038427),
 ('feature_48', 0.008454526),
 ('feature_50', 0.008134796),
 ('feature_51', 0.008436712),
 ('feature_52', 0.0074389745),
 ('feature_53', 0.008460813),
 ('feature_54', 0.008043858),
 ('feature_55',

In [64]:

# Fit model using each importance as a threshold
thresholds = sort(model.feature_importances_)
for thresh in thresholds:
   # select features using threshold
    selection = SelectFromModel(model, threshold=thresh, prefit=True)
    select_X_train = selection.transform(X_train)
    # train model
    model = XGBClassifier()
    selection_model.fit(select_X_train, y_train)
    # eval model
    select_X_test = selection.transform(X_test)
    predictions = selection_model.predict(select_X_test)
    accuracy = accuracy_score(y_test, predictions)
    print("Thresh=%.3f, n=%d, Accuracy: %.2f%%" % (thresh, select_X_train.shape[1], accuracy*100.0))


[18:38:03] INFO: ../src/tree/updater_prune.cc:101: tree pruning end, 72 extra nodes, 0 pruned nodes, max_depth=6
[18:38:03] INFO: ../src/tree/updater_prune.cc:101: tree pruning end, 76 extra nodes, 0 pruned nodes, max_depth=6
[18:38:03] INFO: ../src/tree/updater_prune.cc:101: tree pruning end, 102 extra nodes, 0 pruned nodes, max_depth=6
[18:38:03] INFO: ../src/tree/updater_prune.cc:101: tree pruning end, 66 extra nodes, 0 pruned nodes, max_depth=6
[18:38:03] INFO: ../src/tree/updater_prune.cc:101: tree pruning end, 104 extra nodes, 0 pruned nodes, max_depth=6
[18:38:03] INFO: ../src/tree/updater_prune.cc:101: tree pruning end, 34 extra nodes, 0 pruned nodes, max_depth=6
[18:38:03] INFO: ../src/tree/updater_prune.cc:101: tree pruning end, 100 extra nodes, 0 pruned nodes, max_depth=6
[18:38:03] INFO: ../src/tree/updater_prune.cc:101: tree pruning end, 90 extra nodes, 0 pruned nodes, max_depth=6
[18:38:03] INFO: ../src/tree/updater_prune.cc:101: tree pruning end, 60 extra nodes, 0 pruned

[18:38:04] INFO: ../src/tree/updater_prune.cc:101: tree pruning end, 84 extra nodes, 0 pruned nodes, max_depth=6
[18:38:04] INFO: ../src/tree/updater_prune.cc:101: tree pruning end, 78 extra nodes, 0 pruned nodes, max_depth=6
[18:38:04] INFO: ../src/tree/updater_prune.cc:101: tree pruning end, 100 extra nodes, 0 pruned nodes, max_depth=6
[18:38:04] INFO: ../src/tree/updater_prune.cc:101: tree pruning end, 78 extra nodes, 0 pruned nodes, max_depth=6
[18:38:04] INFO: ../src/tree/updater_prune.cc:101: tree pruning end, 80 extra nodes, 0 pruned nodes, max_depth=6
[18:38:04] INFO: ../src/tree/updater_prune.cc:101: tree pruning end, 100 extra nodes, 0 pruned nodes, max_depth=6
[18:38:04] INFO: ../src/tree/updater_prune.cc:101: tree pruning end, 68 extra nodes, 0 pruned nodes, max_depth=6
[18:38:04] INFO: ../src/tree/updater_prune.cc:101: tree pruning end, 44 extra nodes, 0 pruned nodes, max_depth=6
[18:38:04] INFO: ../src/tree/updater_prune.cc:101: tree pruning end, 98 extra nodes, 0 pruned 

ValueError: The underlying estimator XGBClassifier has no `coef_` or `feature_importances_` attribute. Either pass a fitted estimator to SelectFromModel or call fit before calling transform.

In [55]:
# fit model to training data
model = XGBClassifier(n_estimators=400, max_depth=7, eta=0.3,missing=None,
    random_state=42,
    tree_method='gpu_hist',
    subsample=0.8,
    colsample_bytree=1,
    verbosity=2)
model.fit(X_train, y_train)

print(model)

XGBClassifier(base_score=0.5, booster='gbtree', colsample_bylevel=1,
              colsample_bynode=1, colsample_bytree=1, eta=0.3, gamma=0,
              gpu_id=0, importance_type='gain', interaction_constraints='',
              learning_rate=0.300000012, max_delta_step=0, max_depth=7,
              min_child_weight=1, missing=None,
              monotone_constraints='(0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0)',
              n_estimators=400, n_jobs=0, num_parallel_tree=1, random_state=42,
              reg_alpha=0, reg_lambda=1, scale_pos_weight=1, subsample=0.8,
              tree_method='gpu_hist', validate_parameters=1, verbosity=2)


In [56]:
y_pred = model.predict(X_test)
predictions = [round(value) for value in y_pred]

In [57]:
accuracy = accuracy_score(y_test, predictions)
print("Accuracy: %.2f%%" % (accuracy * 100.0))

Accuracy: 73.39%
